### Preprocessing

In [7]:
import numpy as np
import pandas as pd
import pandas_profiling as pp
import warnings
warnings.filterwarnings('ignore')

from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import StratifiedKFold, cross_val_score, GridSearchCV

In [2]:
train = pd.read_csv('./train.csv', sep='\t')
test = pd.read_csv('./test.csv', sep='\t')

In [3]:
train.shape

(30500, 347)

In [4]:
train.head()

Unnamed: 0  0  1  2  3  4  5  6         7  8 ...        336  337  338  339  \
0           0  1  1  0  0  0  0  0  0.090909  0 ...   0.221395    0    1    0   
1           1  1  1  0  0  1  0  0  0.090909  0 ...   0.241508    0    1    0   
2           2  0  1  0  0  1  0  0  0.090909  0 ...   0.123067    0    1    0   
3           3  0  1  0  0  1  0  0  0.136364  0 ...   0.296065    0    0    1   
4           4  0  1  0  0  1  0  0  0.136364  0 ...   0.178956    0    0    1   

   340       341  342  343  344  345  
0    0  0.222222    1    1    1    1  
1    0  0.111111    1    1    1    0  
2    0  0.444444    1    1    1    1  
3    0  0.222222    1    1    1    0  
4    0  0.111111    1    1    1    1  

[5 rows x 347 columns]

In [5]:
test.tail()

Unnamed: 0   0  1  2  3  4  5  6         7  8 ...        336  337  338  \
4161        4161 NaN  1  0  0  0  0  0  0.090909  0 ...   0.450414    1    0   
4162        4162 NaN  1  0  0  1  0  0  0.090909  0 ...   0.251114    0    1   
4163        4163 NaN  1  0  0  0  0  0  0.090909  0 ...   0.450414    1    0   
4164        4164 NaN  1  0  0  0  0  0  0.136364  0 ...   0.450414    1    0   
4165        4165 NaN  1  0  0  0  0  0  0.090909  0 ...   0.109160    0    0   

      339  340  341  342  343  344  345  
4161    0    0  0.0    0    0    0    1  
4162    0    0  0.0    1    1    1    1  
4163    0    0  0.0    1    1    1    0  
4164    0    0  0.0    1    1    1    1  
4165    0    0  0.0    1    1    1    0  

[5 rows x 347 columns]

In [48]:
pp.ProfileReport(train)

In [49]:
pp.ProfileReport(test)

In [100]:
features = list(train.columns)

#remove index and target
features.remove('Unnamed: 0')
features.remove('0')

print('Length of features {}'.format(len(features)))

Length of features 345


In [ ]:
# removing features which have high percent of zeros
for col in features:
    if max(train[col].value_counts(normalize=True)) <= 0.98:
        features.remove(col)

#some information
print('Length of features {}'.format(len(features)))

In [101]:
# removing correlated features
for col1 in features:
    for col2 in features:
        if col1 != col2 and abs(train[col1].corr(train[col2])) > 0.9:
            print('{} is highly correlated with {}, corr = {}'.format(col1, col2, train[col1].corr(train[col2])))
            features.remove(col2)
print('Length of features {}'.format(len(features)))

1 is highly correlated with 2, corr = -0.9962003989677012
1 is highly correlated with 9, corr = -0.9962003989677012
17 is highly correlated with 153, corr = 1.0
20 is highly correlated with 158, corr = 0.9367681845579977
22 is highly correlated with 165, corr = 0.9962742707490895
24 is highly correlated with 179, corr = 0.9444884593440603
26 is highly correlated with 180, corr = 0.9938509737758875
35 is highly correlated with 146, corr = 0.9666765496395434
39 is highly correlated with 148, corr = 0.9557619731331972
110 is highly correlated with 117, corr = 0.9176426229830209
112 is highly correlated with 119, corr = 0.9096317280498002
115 is highly correlated with 122, corr = 0.9898753708577486
204 is highly correlated with 206, corr = 0.9284310215061199
298 is highly correlated with 323, corr = 0.9369096084046372
298 is highly correlated with 325, corr = 0.9253053542708095
298 is highly correlated with 333, corr = 0.9626232029883194
298 is highly correlated with 335, corr = 0.98622514

## Logistic Regression

* all features  
Validation Score : **0.7250382063826473**  
LB Score : **0.65751746**
  
* non-zeroes features   
Validation Score : **0.7096617046720934**

* non-correlated features  
Validation Score : **0.725041075095092**  
LB Score : **0.65751746**


In [86]:
%%time

X = train[features] 
y = train['0']

sk = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

lg = LogisticRegression(class_weight='balanced', random_state=42)

parameters = {
    'C': (0.01, 1)
}


grid_search = GridSearchCV(
    estimator=lg, 
    param_grid=parameters, 
    scoring ='roc_auc', 
    cv=sk
)

grid_search = grid_search.fit(X, y)
print(grid_search.best_params_)
print(grid_search.best_score_)

{'C': 1}
0.7250382063826473
CPU times: user 31.3 s, sys: 4.84 s, total: 36.2 s
Wall time: 30.9 s


In [87]:
# create submission
X_test = test[features]
y_pred = grid_search.best_estimator_.predict(X_test)

pred_df = pd.DataFrame(test['Unnamed: 0'])
pred_df['_VAL_'] = y_pred
pred_df.columns = ['_ID_', '_VAL_']
pred_df.to_csv('logreg_all_features.csv', index=False)

## Bagging on Log Regression

```
{'max_samples': 0.5, 'base_estimator__C': 1, 'max_features': 0.9}
```
* non-corelated features  
Validation Score : **0.7259043486607948**
* all features  
Validation Score : **0.7257331912888031**  
LB Score : **0.66241462**


In [88]:
from sklearn.ensemble import BaggingClassifier

In [102]:
%%time

X = train[features] 
y = train['0']

sk = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

lg = LogisticRegression(class_weight='balanced', random_state=42)

parameters = {
    'max_features': [0.9], 
    'max_samples': [0.5], 
    'base_estimator__C': [1]
}

bg = BaggingClassifier(base_estimator=lg, random_state=42, n_estimators=25)


grid_search = GridSearchCV(
    estimator=bg, 
    param_grid=parameters, 
    scoring ='roc_auc', 
    cv=sk,
    verbose=2,
    n_jobs=-1
)

grid_search = grid_search.fit(X, y)
print(grid_search.best_params_)
print(grid_search.best_score_)

Fitting 5 folds for each of 1 candidates, totalling 5 fits
[CV] base_estimator__C=1, max_samples=0.5, max_features=0.9 ..........
[CV] base_estimator__C=1, max_samples=0.5, max_features=0.9 ..........
[CV] base_estimator__C=1, max_samples=0.5, max_features=0.9 ..........
[CV] base_estimator__C=1, max_samples=0.5, max_features=0.9 ..........
[CV]  base_estimator__C=1, max_samples=0.5, max_features=0.9, total= 1.9min
[CV] base_estimator__C=1, max_samples=0.5, max_features=0.9 ..........
[CV]  base_estimator__C=1, max_samples=0.5, max_features=0.9, total= 1.9min
[CV]  base_estimator__C=1, max_samples=0.5, max_features=0.9, total= 1.9min
[CV]  base_estimator__C=1, max_samples=0.5, max_features=0.9, total= 1.9min
[CV]  base_estimator__C=1, max_samples=0.5, max_features=0.9, total= 1.0min


[Parallel(n_jobs=-1)]: Done   5 out of   5 | elapsed:  3.0min finished


{'max_samples': 0.5, 'base_estimator__C': 1, 'max_features': 0.9}
0.7259043486607948
CPU times: user 1min 15s, sys: 672 ms, total: 1min 16s
Wall time: 4min 14s


In [94]:
import pickle

# dump bagging model
file_name = 'bagging_model'
best_classifier = grid_search.best_estimator_
with open(file_name, 'wb') as file:
    pickle.dump(best_classifier, file)

In [95]:
# load the model from disk
loaded_model = pickle.load(open(filename, 'rb'))

In [103]:
# create submission csv
X_test = test[features]
y_pred = grid_search.best_estimator_.predict(X_test)

pred_df = pd.DataFrame(test['Unnamed: 0'])
pred_df['_VAL_'] = y_pred
pred_df.columns = ['_ID_', '_VAL_']
pred_df.to_csv('bagging_all_features.csv', index=False)

## Random Forest

## Ensemble

## Stacking